<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"></ul></div>

In [63]:
import pandas as pd
from librosa.core import resample, load
from librosa.util import fix_length
from librosa import feature
import numpy as np
from tqdm import tqdm
from tqdm.notebook import tqdm as nb_tqdm
import seaborn as sns
from matplotlib import pyplot as plt
import umap
import plotly.express as px

In [9]:
df = pd.read_csv('full.csv',index_col=0)
df = df.fillna(0)

In [10]:
df.head(10)

path  \
0  ./Samples/MDLib2.2/Sorted/Snare SNoff/Buzz/ST_...   
1  ./Samples/MDLib2.2/Sorted/Snare SNoff/Buzz/DI_...   
2  ./Samples/MDLib2.2/Sorted/Snare SNoff/Buzz/IN_...   
3  ./Samples/MDLib2.2/Sorted/Snare SNoff/Buzz/ST_...   
4  ./Samples/MDLib2.2/Sorted/Snare SNoff/Buzz/MN_...   
5  ./Samples/MDLib2.2/Sorted/Snare SNoff/Buzz/IN_...   
6  ./Samples/MDLib2.2/Sorted/Snare SNoff/Buzz/DI_...   
7  ./Samples/MDLib2.2/Sorted/Snare SNoff/Buzz/MN_...   
8  ./Samples/MDLib2.2/Sorted/Snare SNoff/Buzz/MN_...   
9  ./Samples/MDLib2.2/Sorted/Snare SNoff/Buzz/ST_...   

                   filename dir_1        dir_2  class_Snare  class_Tom dir_3  \
0  ST_Snare_Buzz_0112.2.wav  Buzz  Snare SNoff          1.0        0.0     0   
1  DI_Snare_Buzz_0224.3.wav  Buzz  Snare SNoff          1.0        0.0     0   
2  IN_Snare_Buzz_0214.1.wav  Buzz  Snare SNoff          1.0        0.0     0   
3  ST_Snare_Buzz_0333.3.wav  Buzz  Snare SNoff          1.0        0.0     0   
4  MN_Snare_Buzz_0111.4.wav  Buzz  Snare SNoff          1.0        0.0     0   
5  IN_Snare_Buzz_0112.3.wav  Buzz  Snare SNoff          1.0        0.0     0   
6  DI_Snare_Buzz_0322.1.wav  Buzz  Snare SNoff          1.0        0.0     0   
7  MN_Snare_Buzz_0321.2.wav  Buzz  Snare SNoff          1.0        0.0     0   
8  MN_Snare_Buzz_0231.2.wav  Buzz  Snare SNoff          1.0        0.0     0   
9  ST_Snare_Buzz_0232.4.wav  Buzz  Snare SNoff          1.0        0.0     0   

   class_Cymbal  subclass_Cymbal_Crash  subclass_Cymbal_Ride  ...  \
0           0.0                    0.0                   0.0  ...   
1           0.0                    0.0                   0.0  ...   
2           0.0                    0.0                   0.0  ...   
3           0.0                    0.0                   0.0  ...   
4           0.0                    0.0                   0.0  ...   
5           0.0                    0.0                   0.0  ...   
6           0.0                    0.0                   0.0  ...   
7           0.0                    0.0                   0.0  ...   
8           0.0                    0.0                   0.0  ...   
9           0.0                    0.0                   0.0  ...   

   subclass_Shaken_Cabasa  class_Clave  class_Timpani  class_Agogo  \
0                     0.0          0.0            0.0          0.0   
1                     0.0          0.0            0.0          0.0   
2                     0.0          0.0            0.0          0.0   
3                     0.0          0.0            0.0          0.0   
4                     0.0          0.0            0.0          0.0   
5                     0.0          0.0            0.0          0.0   
6                     0.0          0.0            0.0          0.0   
7                     0.0          0.0            0.0          0.0   
8                     0.0          0.0            0.0          0.0   
9                     0.0          0.0            0.0          0.0   

   class_Triangle  class_Djembe  class_Tabla  class_Darbuka  \
0             0.0           0.0          0.0            0.0   
1             0.0           0.0          0.0            0.0   
2             0.0           0.0          0.0            0.0   
3             0.0           0.0          0.0            0.0   
4             0.0           0.0          0.0            0.0   
5             0.0           0.0          0.0            0.0   
6             0.0           0.0          0.0            0.0   
7             0.0           0.0          0.0            0.0   
8             0.0           0.0          0.0            0.0   
9             0.0           0.0          0.0            0.0   

   subclass_Shaken_Maracas  class_Cajon  
0                      0.0          0.0  
1                      0.0          0.0  
2                      0.0          0.0  
3                      0.0          0.0  
4                      0.0          0.0  
5                      0.0          0.0  
6                      0.0     

In [12]:
features = pd.DataFrame()

In [19]:
SR=22050
#data = data.sample(frac=0.2)
for index, file in tqdm(zip(df.index, df['path']), total=len(df.index), position=0, leave=True):
    try:
        sound, _ = load(file, sr=SR)
    except:
        continue
    
    rms = feature.rms(sound)[0]
     #normalize by rms of attack frame
    rms_centroid = (rms * np.arange(len(rms))).sum() / rms.sum()
    features.loc[index, 'rms_centroid'] = rms_centroid
    
    sound = sound/rms.max()
    sound = fix_length(sound, 1024*(SR//1024))
    
    zero_cr = feature.zero_crossing_rate(sound)[0]
    columns = ['zero_cr_' + str(x) for x in range(zero_cr.shape[0])]
    for col, value in zip(columns, zero_cr):
        features.loc[index, col] = value
        
    spect_cent = feature.spectral_centroid(sound, sr=SR)[0]
    columns = ['spect_cent_' + str(x) for x in range(spect_cent.shape[0])]
    for col, value in zip(columns, spect_cent):
        features.loc[index, col] = value
        
    spect_ro = feature.spectral_rolloff(sound, sr=SR)[0]
    columns = ['spect_ro_' + str(x) for x in range(spect_ro.shape[0])]
    for col, value in zip(columns, spect_ro):
        features.loc[index, col] = value
        
    rms = feature.rms(sound)[0]
    columns = ['rms_' + str(x) for x in range(rms.shape[0])]
    for col, value in zip(columns, rms):
        #features.loc[index, col] = value
        features.loc[index, 'norm_'+ col] = value
    
        
    spect_cont = feature.spectral_contrast(sound, sr=SR)
    for i in range (spect_cont.shape[0]):
        for j in range (spect_cont.shape[1]):
            col = 'spec_cont_' + str(i) + '_' + str(j)
            features.loc[index, col] = spect_cont[i][j]

 74%|███████▍  | 15436/20870 [37:07<11:32,  7.84it/s] /home/guillaume/miniconda3/lib/python3.7/site-packages/librosa/core/audio.py:161: UserWarning: PySoundFile failed. Trying audioread instead.
  warnings.warn('PySoundFile failed. Trying audioread instead.')


NoBackendError: 

In [20]:
features.to_csv('features.csv')

In [21]:
df.columns

Index(['path', 'filename', 'dir_1', 'dir_2', 'class_Snare', 'class_Tom',
       'dir_3', 'class_Cymbal', 'subclass_Cymbal_Crash',
       'subclass_Cymbal_Ride', 'class_Hat', 'class_Kick', 'subclass_Hat_Open',
       'subclass_Hat_Close', 'class_Bongo', 'subclass_Cymbal_Chinese',
       'subclass_Cymbal_Splash', 'class_Conga', 'class_Gong', 'class_Cowbell',
       'class_Rimshot', 'class_Clap', 'class_Shaken', 'subclass_Shaken_Shaker',
       'subclass_Shaken_Tambourin', 'subclass_Shaken_Cabasa', 'class_Clave',
       'class_Timpani', 'class_Agogo', 'class_Triangle', 'class_Djembe',
       'class_Tabla', 'class_Darbuka', 'subclass_Shaken_Maracas',
       'class_Cajon'],
      dtype='object')

In [57]:
classes = [c for c in df.columns if c.startswith('class_')]
cymb_classes = [c for c in df.columns if c.startswith('subclass_Cymbal')]
shak_classes = [c for c in df.columns if c.startswith('subclass_Shaken')]
hat_classes = [c for c in df.columns if c.startswith('subclass_Hat')]

all_classes = classes + cymb_classes + shak_classes + hat_classes

In [101]:
cymb_classes

['subclass_Cymbal_Crash',
 'subclass_Cymbal_Ride',
 'subclass_Cymbal_Chinese',
 'subclass_Cymbal_Splash']

In [96]:
class_df = pd.DataFrame()

class_df['class'] = df[all_classes].idxmax(axis=1)
cymbales = (df['class_Cymbal'] == 1) & df[cymb_classes].sum(axis=0) > 0
class_df.loc[cymbales, 'class'] = df.loc[cymbales, cymb_classes].idxmax(axis=1)
shaken = (df['class_Shaken'] == 1) & df[shak_classes].sum(axis=0) > 0
class_df.loc[shaken, 'class'] = df.loc[shaken, shak_classes].idxmax(axis=1)
hats = (df['class_Hat'] == 1) & df[hat_classes].sum(axis=0) > 0
class_df.loc[hats, 'class'] = df.loc[hats, hat_classes].idxmax(axis=1)
# class_df['class'] = df[hat_classes + ['class_Hat']].idxmax(axis=1)

In [103]:
class_df[class_df['class'].startsWith('subclass')].sample(10)

AttributeError: 'Series' object has no attribute 'startsWith'

In [37]:
reducer = umap.UMAP()
embedding = reducer.fit_transform(features)

In [191]:
class_df = class_df.loc[features.index]

In [83]:
filename = df.loc[features.index,'path']
embedding_df = pd.DataFrame({
    'x': embedding[:, 0],
    'y': embedding[:, 1],
    'class': class_df['class'].values,
    'file': filename    
                         })

In [85]:
fig = px.scatter(
    embedding_df,
    x='x',
    y='y',
    color='class',
    hover_data=['file']
)
fig.show()

In [104]:
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers

In [215]:
class Sampling(layers.Layer):
    """Uses (z_mean, z_log_var) to sample z, the vector encoding a digit."""

    def call(self, inputs):
        z_mean, z_log_var = inputs
        batch = tf.shape(z_mean)[0]
        dim = tf.shape(z_mean)[1]
        epsilon = tf.keras.backend.random_normal(shape=(batch, dim))
        return z_mean + tf.exp(0.5 * z_log_var) * epsilon

In [252]:
latent_dim = 20
input_dim = features.shape[1]

encoder_inputs = keras.Input(shape=(input_dim))
x = layers.Dense(64, activation="relu")(encoder_inputs)
x = layers.Dense(32, activation="relu")(x)
x = layers.Dense(16, activation="relu")(x)
z_mean = layers.Dense(latent_dim, name="z_mean")(x)
z_log_var = layers.Dense(latent_dim, name="z_log_var",
                         bias_initializer='zeros', kernel_initializer='zeros',
                         activity_regularizer='l1')(x)
z = Sampling()([z_mean, z_log_var])
encoder = keras.Model(encoder_inputs, [z_mean, z_log_var, z], name="encoder")
encoder.summary()

Model: "encoder"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_42 (InputLayer)           [(None, 474)]        0                                            
__________________________________________________________________________________________________
dense_124 (Dense)               (None, 64)           30400       input_42[0][0]                   
__________________________________________________________________________________________________
dense_125 (Dense)               (None, 32)           2080        dense_124[0][0]                  
__________________________________________________________________________________________________
dense_126 (Dense)               (None, 16)           528         dense_125[0][0]                  
____________________________________________________________________________________________

In [253]:
latent_inputs = keras.Input(shape=(latent_dim,))
#x = layers.BatchNormalization()(latent_inputs)
x = layers.Dense(32, activation="relu")(latent_inputs)
x = layers.Dense(64, activation="relu")(x)
x = layers.Dense(128, activation="relu")(x)
decoder_outputs = layers.Dense(input_dim, activation="relu")(x)
decoder = keras.Model(latent_inputs, decoder_outputs, name="decoder")
decoder.summary()

Model: "decoder"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_43 (InputLayer)        [(None, 20)]              0         
_________________________________________________________________
dense_127 (Dense)            (None, 32)                672       
_________________________________________________________________
dense_128 (Dense)            (None, 64)                2112      
_________________________________________________________________
dense_129 (Dense)            (None, 128)               8320      
_________________________________________________________________
dense_130 (Dense)            (None, 474)               61146     
Total params: 72,250
Trainable params: 72,250
Non-trainable params: 0
_________________________________________________________________


In [254]:
class VAE(keras.Model):
    def __init__(self, encoder, decoder, **kwargs):
        super(VAE, self).__init__(**kwargs)
        self.encoder = encoder
        self.decoder = decoder

    def train_step(self, data):
        if isinstance(data, tuple):
            data = data[0]
        with tf.GradientTape() as tape:
            z_mean, z_log_var, z = encoder(data)
            reconstruction = decoder(z)
            reconstruction_loss = tf.reduce_mean(
                keras.losses.MSE(data, reconstruction)
            )
            #reconstruction_loss *= features.shape[1]
            kl_loss = 1 + z_log_var - tf.square(z_mean) - tf.exp(z_log_var)
            kl_loss = tf.reduce_mean(kl_loss)
            kl_loss *= -0.5
            total_loss = reconstruction_loss + kl_loss
        grads = tape.gradient(total_loss, self.trainable_weights)
        self.optimizer.apply_gradients(zip(grads, self.trainable_weights))
        return {
            "loss": total_loss,
            "reconstruction_loss": reconstruction_loss,
            "kl_loss": kl_loss,
        }

In [255]:

vae = VAE(encoder, decoder)
vae.compile(optimizer=keras.optimizers.Adam(learning_rate=0.0001))
vae.fit(features.values, epochs=30, batch_size=128)

Epoch 1/30
121/121 [==============================] - 2s 14ms/step - loss: 3144277.6189 - reconstruction_loss: 2938757.3873 - kl_loss: 205520.2358
Epoch 2/30
121/121 [==============================] - 2s 16ms/step - loss: 1591926.7264 - reconstruction_loss: 1244113.6255 - kl_loss: 347813.1013
Epoch 3/30
121/121 [==============================] - 2s 16ms/step - loss: 1132670.9298 - reconstruction_loss: 1002147.0446 - kl_loss: 130523.8824
Epoch 4/30
121/121 [==============================] - 2s 16ms/step - loss: 1062439.4985 - reconstruction_loss: 991050.3776 - kl_loss: 71389.1170
Epoch 5/30
121/121 [==============================] - 2s 15ms/step - loss: 1031677.5830 - reconstruction_loss: 983940.8043 - kl_loss: 47736.7821
Epoch 6/30
121/121 [==============================] - 2s 15ms/step - loss: 1003627.4385 - reconstruction_loss: 965310.9944 - kl_loss: 38316.4422
Epoch 7/30
121/121 [==============================] - 2s 16ms/step - loss: 920714.9641 - reconstruction_loss: 879793.2326 - 

In [256]:
_, _, features_vae = encoder.predict(features.values)

In [257]:
features_vae.shape

(15436, 20)

In [259]:
features_vae_df = pd.DataFrame(features_vae, index=features.index)

In [261]:
vae_reducer = umap.UMAP()
embedding = vae_reducer.fit_transform(features_vae)

In [262]:
embedding.shape, filename.shape, class_df['class'].shape

((15436, 2), (15436,), (15436,))

In [263]:
embedding_df = pd.DataFrame({
    'x': embedding[:, 0],
    'y': embedding[:, 1],
    'class': class_df['class'].values,
    'file': filename    
                         })
fig = px.scatter(
    embedding_df,
    x='x',
    y='y',
    color='class',
    hover_data=['file']
)
fig.show()